# News

## Tagesschau API

In [1]:
import json
import requests
from bs4 import BeautifulSoup


class TagesschauAPI:
    def __init__(self):
        self.base_url = "https://www.tagesschau.de/api2"

    def get_news_for_sector(self, sector: str) -> dict:
        url = f"{self.base_url}/news/"
        regions = ",".join([str(i) for i in range(1, 16)])
        result = requests.get(url=url, params={"regions": regions, "ressort": sector})
        return result.json()

    def custom_search(self, query: str) -> dict:
        url = f"{self.base_url}/search/"
        result = requests.get(url=url, params={"searchText": query})
        return result.json()

    def get_news_details_text(self, url: str) -> dict:
        content = requests.get(url)
        soup = BeautifulSoup(content.text, features="html.parser")

        return " ".join(
            [elem.text.replace("\n", " ") for elem in soup.find_all("p")][1:]
        )


tagesschau = TagesschauAPI()

data = tagesschau.get_news_for_sector("wirtschaft")
with open("./data/temp.json", "w+", encoding="utf-8") as file:
    json.dump(data, file, ensure_ascii=False)

In [2]:
from tqdm import tqdm
import pandas as pd


news = []
for news_article in tqdm(data["news"]):
    info = {
        "id": news_article["externalId"],
        "title": news_article["title"],
        "date": news_article["date"],
        "source_url": news_article["detailsweb"],
        "text": tagesschau.get_news_details_text(news_article["detailsweb"]),
    }
    news.append(info)

df = pd.DataFrame(news)
df.head()

100%|██████████| 54/54 [00:12<00:00,  4.49it/s]


id  \
0  f6f64332-a721-43b2-a6e1-0d64be343712   
1  20869ff8-54ac-436d-964d-8d45032467a9   
2  467c0c06-6332-4ab6-8678-666c35388850   
3  83e6a13f-2731-41e8-8298-212263e59887   
4  a59fb7be-04d1-4c5b-ba8b-b2cafbd6aba7   

                                               title  \
0         Bezahlen mit der Karte - bald ohne Maestro   
1                  Durchschnaufen an der Wall Street   
2  EVG und Deutsche Bahn vertagen sich auf kommen...   
3      Wie der Euro von steigenden Zinsen profitiert   
4  Intel will Chipfabrik im polnischen Breslau bauen   

                            date  \
0  2023-06-17T07:14:11.918+02:00   
1  2023-06-16T22:22:05.873+02:00   
2  2023-06-16T21:53:30.404+02:00   
3  2023-06-16T14:57:03.999+02:00   
4  2023-06-16T14:00:01.950+02:00   

                                          source_url  \
0  https://www.tagesschau.de/wirtschaft/verbrauch...   
1  https://www.tagesschau.de/wirtschaft/finanzen/...   
2  https://www.tagesschau.de/wirtschaft/unternehm...   
3  https://www.tagesschau.de/wirtschaft/finanzen/...   
4  https://www.tagesschau.de/wirtschaft/unternehm...   

                                                text  
0   Das Maestro-Logo gehörte bislang normalerweis...  
1   Nach einer ereignisreichen Woche haben die US...  
2   Die Tarifverhandlungen zwischen Deutscher Bah...  
3   Nach der jüngsten Zinserhöhung der EZB ist de...  
4   Der US-Konzern Intel plant eine neue Chipfabr...

In [3]:
df.to_json("./data/news.json", orient="records", force_ascii=False)

In [4]:
from utils.mongodb.mongo import MongoConnector

connector = MongoConnector(
    hostname="localhost",
    database="transparenzregister",
    username="root",
    password="pR0R0v2e2",
)

In [6]:
from utils.mongodb.mongo import MongoNewsService

service = MongoNewsService(connector)
service.get_all()

[]

In [7]:
from models.News import News

# service.insert(
# News(
# "abc", "Hallo Welt", "heute", "what does the fox say", "https://localhost:8080"
# )
# )

In [11]:
news

[{'id': 'f6f64332-a721-43b2-a6e1-0d64be343712',
  'title': 'Bezahlen mit der Karte - bald ohne Maestro',
  'date': '2023-06-17T07:14:11.918+02:00',
  'source_url': 'https://www.tagesschau.de/wirtschaft/verbraucher/girocard-maestro-mastercard-visa-zahlungssystem-100.html',
  'text': ' Das Maestro-Logo gehörte bislang normalerweise zur Girocard, der früheren EC-Karte. Nun wird Maestro nach und nach aufs internationale Zahlungssystem von Mastercard und Visa umgestellt. Was dabei zu beachten ist.   Manche Kunden deutscher Banken und Sparkassen sind verunsichert. Denn ab dem 1. Juli wird das gewohnte Maestro-Logo bei vielen neuen Girokarten - den ehemaligen EC-Karten - nicht mehr auf der Vorderseite prangen. Keinen Grund zur Aufregung sieht Oliver Hommel von Euro Kartensysteme in Frankfurt, dem Gemeinschaftsunternehmen der deutschen Banken und Sparkassen, das sich um die Einsatzmöglichkeiten der Girocard in ganz Europa kümmert: "Die bestehenden Karten bleiben bis zum Ablaufdatum gültig und 

In [13]:
for article in tqdm(news):
    news_article = News(**article)
    if service.get_by_id(news_article.id) is None:
        service.insert(news_article)

100%|██████████| 54/54 [00:00<00:00, 670.01it/s]


In [ ]:
service.get_by_id("abc")

News(id='abc', title='Hallo Welt', date='heute', text='what does the fox say')

### Handelsblatt RSS Feed

In [1]:
import requests
import xmltodict
from bs4 import BeautifulSoup


class HandelsblattRSS:
    def __init__(self):
        self.base_url = "https://www.handelsblatt.com/contentexport/feed"

    def get_news_for_category(self, category: str = "unternehmen") -> dict:
        url = f"{self.base_url}/{category}"
        result = requests.get(url=url)
        if result.status_code == 200:
            return xmltodict.parse(result.text)["rss"]["channel"]["item"]
        return None

    def get_news_details_text(self, url: str) -> dict:
        content = requests.get(url)
        soup = BeautifulSoup(content.text, features="html.parser")

        return " ".join(
            [elem.text.replace("\n", " ") for elem in soup.find_all("p")][:]
        )

In [2]:
handelsblatt = HandelsblattRSS()

items = handelsblatt.get_news_for_category()
print(items)
# from utils.mongodb.mongo import MongoConnector, MongoNewsService

# connector = MongoConnector(
#     hostname="trisnol.tech",
#     database="transparenzregister",
#     username="root",
#     password="pR0R0v2e2",
# )

# service = MongoNewsService(connector)

[{'title': 'BMP Greengas: Gläubiger fordern knapp eine Dreiviertelmilliarde Euro von insolventer EnBW-Tochter', 'link': 'https://www.handelsblatt.com/unternehmen/energie/bmp-greengas-glaeubiger-fordern-mehr-als-700-millionen-euro-von-insolventer-enbw-tochter/29394600.html', 'description': 'BMP Greengas verkaufte Biomethan an Stadtwerke und Energieversorger in ganz Deutschland. Die Insolvenz des Gashändlers könnte die öffentliche Hand Hunderte Millionen Euro kosten.', 'category': 'Energie', 'pubDate': 'Fri, 15 Sep 2023 20:26:51 +0200', 'guid': 'https://www.handelsblatt.com/29394600.html', 'content:encoded': '<a href="https://www.handelsblatt.com/unternehmen/energie/bmp-greengas-glaeubiger-fordern-mehr-als-700-millionen-euro-von-insolventer-enbw-tochter/29394600.html"><img alt="" src="https://www.handelsblatt.com/images/biogasanlage/29394638/3-format2020.jpg"/></a>BMP Greengas verkaufte Biomethan an Stadtwerke und Energieversorger in ganz Deutschland. Die Insolvenz des Gashändlers könnte

In [18]:
from datetime import datetime

d = items[0]["pubDate"]
datetime.strptime(d, "%a, %d %b %Y %H:%M:%S %z").strftime("%Y-%m-%dT%H:%M:%S%z")

'2023-06-27T09:20:32+0200'

In [19]:
from datetime import datetime
from tqdm import tqdm
import pandas as pd


news = []
for news_article in tqdm(items):
    info = {
        "id": news_article["guid"],
        "title": news_article["title"],
        "date": datetime.strptime(
            news_article["pubDate"], "%a, %d %b %Y %H:%M:%S %z"
        ).strftime("%Y-%m-%dT%H:%M:%S%z"),
        "source_url": news_article["link"],
        "text": handelsblatt.get_news_details_text(news_article["link"]),
    }
    news.append(info)

df = pd.DataFrame(news)
df.head()

100%|██████████| 50/50 [01:04<00:00,  1.30s/it]


id  \
0  https://www.handelsblatt.com/29227224.html   
1  https://www.handelsblatt.com/29226410.html   
2  https://www.handelsblatt.com/29226522.html   
3  https://www.handelsblatt.com/29228524.html   
4  https://www.handelsblatt.com/29228272.html   

                                               title  \
0  Dieselskandal: Ex-Audi-Chef Rupert Stadler zu ...   
1  Luftfahrt: Größer, reichweitenstärker – aber n...   
2  Asien: Deutsche Unternehmen wetten auf den Ind...   
3  Elektromobilität: US-Elektroautohersteller Lor...   
4  US-Konzern: „Gewaltige Komplexität“ – BGH prüf...   

                       date  \
0  2023-06-27T09:20:32+0200   
1  2023-06-27T16:28:53+0200   
2  2023-06-27T00:30:00+0200   
3  2023-06-27T18:45:29+0200   
4  2023-06-27T16:23:03+0200   

                                          source_url  \
0  https://www.handelsblatt.com/unternehmen/indus...   
1  https://www.handelsblatt.com/unternehmen/hande...   
2  https://www.handelsblatt.com/politik/internati...   
3  https://www.handelsblatt.com/unternehmen/indus...   
4  https://www.handelsblatt.com/unternehmen/hande...   

                                                text  
0  Der frühere Audi-Chef wurde wegen Betrugs zu e...  
1  Honda Aircraft arbeitet an einem Privatflugzeu...  
2  Unternehmen gehen von einer positiven wirtscha...  
3  Das Start-up plante die Massenproduktion mit e...  
4  Das Kartellamt stufte den US-Konzern vergangen...

In [23]:
from models.News import News

for article in tqdm(news):
    news_article = News(**article)
    if service.get_by_id(news_article.id) is None:
        service.insert(news_article)

100%|██████████| 50/50 [00:00<00:00, 81.98it/s]
